In [1]:
# Import needed libraries

import concurrent.futures
import time
import glob
import os
from dataclasses import dataclass

try:
    from moviepy.video.io.VideoFileClip import VideoFileClip
except:
    !pip install moviepy
    from moviepy.video.io.VideoFileClip import VideoFileClip

#### Our project works on word level prediction unlike sentence level classifiers

In [2]:
# Define our data class to handle words data

@dataclass()
class WordInstance:
    """Class for keeping track of each word"""
    name: str
    start_time: str
    end_time: str

#### Defining the words present in the grid corpus dataset and the framerate:

We have 6 categories which are:

1. Commands
2. prepositions
3. Colors
4. Adverbs
5. Alphabet
6. Numbers

In [3]:
commands = ['bin', 'lay', 'place', 'set']
prepositions = ['at', 'by', 'in', 'with']
colors = ['blue', 'green', 'red', 'white']
adverbs = ['again', 'now', 'please', 'soon']
alphabet = [chr(x) for x in range(ord('a'), ord('z') + 1)]
numbers = ['one', 'two', 'three', 'four', 'five', 'six', 'seven', 'eight', 'nine']

FPS = 25 #Frames Per Second
dataSetPath = 'GridCorpus_DataSet/'
numberSpeakers = 20

#### To segment each video and build the resultant segmented dataset, we use the following Helper Functions:

In [4]:
"""
    Produces the align path name for each video for a certain speaker based on the videos path
    Arguments:
        Path: String of the files location
    Returns:
        Align File path
"""
def getAlignFileName(Path):
    tempPath = Path.split("/")
    print(tempPath)
    newPath = tempPath[0] + '/align/' + (tempPath[-1].split('\\')[1]).split('.')[0] + '.align'
    print(newPath)
    return newPath


"""
    Extracts each align file into a list of dataclasses
    Arguments:
        fileName: String containing the file's name
    Returns:
        List of Data classes with the word and timings
"""
def extractWordTimingFromVideo(filename):
    lines = open(filename).read().splitlines()
    wordsWithTimings = []
    for line in lines:
        temp = line.split()
        wordsWithTimings.append(WordInstance(temp[2], temp[0], temp[1]))
    return wordsWithTimings

"""
    Function that cuts video from a given interval
    Arguments:
        videoPath: String with the Video's Path
        fileName: Name of the newly cut video
        start_time: Starting time of the word in Video
        end_time: Ending time f the word in video
    
"""
def cutVideo(videoPath, fileName, start_time, end_time):
    with VideoFileClip(videoPath, audio=False) as video:
        new = video.subclip(start_time, end_time)
        new.write_videofile(fileName)
        new.close()

"""
    Create dataset segmentation directories for each speaker
    Arguments:
        speakerNumber: Number of the speaker in our Dataset

"""
def createDataSetDirectories(speakerNumber):
    """Function to create dataset segmentation directories for each individual speaker"""
    dirName = 'Extracted_Videos/S{}/Commands/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Prepositions/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Colors/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Adverb/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Alphabet/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Numbers/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

    dirName = 'Extracted_Videos/S{}/Silence/'.format(speakerNumber)
    if not os.path.exists(dirName):
        os.makedirs(dirName)

"""
    Separate a single video into its constituent words and place them in their relevant folders
    Arguments:
        videoPath: String containing the path of the video
        alignFilePath: Path of the designated File path
        speakerNumber: Number of the speaker in our database


"""
def segmentSingleVideo(videoPath, alignFilePath, speakerNumber):
    wordTimings = extractWordTimingFromVideo(alignFilePath)

    createDataSetDirectories(speakerNumber)

    for word in wordTimings:

        start_time = round((float(word.start_time) / (FPS * 1000)), 3)
        end_time = round((float(word.end_time) / (FPS * 1000)), 3)

        if word.name in commands:
            new_index = len(os.listdir('Extracted_Videos/S{}/Commands/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Commands/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name in prepositions:
            new_index = len(os.listdir('Extracted_Videos/S{}/Prepositions/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Prepositions/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name in colors:
            new_index = len(os.listdir('Extracted_Videos/S{}/Colors/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Colors/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name in numbers:
            new_index = len(os.listdir('Extracted_Videos/S{}/Numbers/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Numbers/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name in adverbs:
            new_index = len(os.listdir('Extracted_Videos/S{}/Adverb/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Adverb/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name in alphabet:
            new_index = len(os.listdir('Extracted_Videos/S{}/Alphabet/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Alphabet/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)

        if word.name == 'sil':
            new_index = len(os.listdir('Extracted_Videos/S{}/Silence/'.format(speakerNumber)))
            fileName = 'Extracted_Videos/S{}/Silence/{}_{}.mp4'.format(speakerNumber, word.name, new_index)
            cutVideo(videoPath, fileName, start_time, end_time)


"""
    Separating the entire dataset into individual word videos
    Arguments:
        Path: String containing the path to our dataset
        numberOfSpeaker: Speaker's Number in our dataset to segment
        
"""
def segmentSpeakerDataSet(Path, numberOfSpeaker):
    videoPath = Path + "video/S{}/".format(numberOfSpeaker) + "*.mpg"
    videosGen = glob.iglob(videoPath)
    
    for i in range(len(os.listdir(videoPath.split('*')[0]))):
        py = next(videosGen)
        segmentSingleVideo(py, getAlignFileName(py), numberOfSpeaker)
    

#### Concurrent Dataset sementation:

In [ ]:
speakerNumber = [x for x in range(1,numberSpeakers + 1)]


with concurrent.futures.ThreadPoolExecutor(max_workers = 5) as executor:
    future_to_segment = {executor.submit(segmentSpeakerDataSet,dataSetPath, numberOfSpeaker): numberOfSpeaker for numberOfSpeaker in speakerNumber}
    
    for future in concurrent.futures.as_completed(future_to_segment):
        numberOfSpeaker = future_to_segment[future]
        
        try:
            data = future.result()
        except Exception as exc:
            print(exc)
            print('Speaker {} generated an exception: {}'.format(numberOfSpeaker, exc))
        else:
            print('Speaker {} is segmented Successfully'.format(numberOfSpeaker))
    

['GridCorpus_DataSet', 'video', 'S1\\bbaf2n.mpg']
GridCorpus_DataSet/align/bbaf2n.align
['GridCorpus_DataSet', 'video', 'S5\\bbae8n.mpg']
GridCorpus_DataSet/align/bbae8n.align
['GridCorpus_DataSet', 'video', 'S2\\bbaf1n.mpg']
GridCorpus_DataSet/align/bbaf1n.align
['GridCorpus_DataSet', 'video', 'S3\\bbaf1s.mpg']
GridCorpus_DataSet/align/bbaf1s.align
['GridCorpus_DataSet', 'video', 'S4\\bbae9n.mpg']
GridCorpus_DataSet/align/bbae9n.align


t:   0%|                                                                              | 0/10 [00:00<?, ?it/s, now=None]

t:   0%|                                                                              | 0/13 [00:00<?, ?it/s, now=None]


                                                                                                                       
                                                                                                                    


                                                                                                              

t:  10%|███████                                                               | 1/10 [00:00<00:00, 13.51it/s, now=None]


t:   7%|████▋                                                                 | 1/15 [00:00<00:00, 16.40it/s, now=None]

                                                                                                                       
                                           

Moviepy - Building video Extracted_Videos/S1/Silence/sil_0.mp4.
Moviepy - Writing video Extracted_Videos/S1/Silence/sil_0.mp4

Moviepy - Building video Extracted_Videos/S5/Silence/sil_0.mp4.
Moviepy - Writing video Extracted_Videos/S5/Silence/sil_0.mp4

Moviepy - Building video Extracted_Videos/S2/Silence/sil_0.mp4.
Moviepy - Building video Extracted_Videos/S3/Silence/sil_0.mp4.
Moviepy - Writing video Extracted_Videos/S2/Silence/sil_0.mp4

Moviepy - Writing video Extracted_Videos/S3/Silence/sil_0.mp4

Moviepy - Building video Extracted_Videos/S4/Silence/sil_0.mp4.
Moviepy - Writing video Extracted_Videos/S4/Silence/sil_0.mp4







t:  20%|██████████████                                                        | 2/10 [00:00<00:00, 15.38it/s, now=None]

t:  15%|██████████▊                                                           | 2/13 [00:00<00:00, 14.08it/s, now=None]


t:  13%|█████████▎                                                            | 2/15 [00:00<00:01, 12.90it/s, now=None]


                                                                                                              

                                                                                                                 



                                                                                                           
t:  83%|█████████████████████████████████████████████████████████▌           | 20/24 [00:00<00:00, 16.92it/s, now=None]





                                                                                                                       


t:  67%|███████████████████████████████████████

Moviepy - Done !
Moviepy - video ready Extracted_Videos/S3/Silence/sil_0.mp4
Moviepy - Done !
Moviepy - video ready Extracted_Videos/S5/Silence/sil_0.mp4
Moviepy - Done !
Moviepy - video ready Extracted_Videos/S4/Silence/sil_0.mp4
Moviepy - Done !
Moviepy - video ready Extracted_Videos/S2/Silence/sil_0.mp4
Moviepy - Done !
Moviepy - video ready Extracted_Videos/S1/Silence/sil_0.mp4


...

t:   0%|                                                                              | 0/22 [00:00<?, ?it/s, now=None]

Moviepy - Done !
Moviepy - video ready Extracted_Videos/S1/Silence/sil_448.mp4
Moviepy - Done !
Moviepy - video ready Extracted_Videos/S4/Silence/sil_450.mp4
Moviepy - Building video Extracted_Videos/S5/Silence/sil_449.mp4.
Moviepy - Writing video Extracted_Videos/S5/Silence/sil_449.mp4



t:   0%|                                                                              | 0/16 [00:00<?, ?it/s, now=None]
                                                                                                                       
t:   5%|███▏                                                                  | 1/22 [00:00<00:02,  7.19it/s, now=None]
                                                                                                                       
t:   9%|██████▎                                                               | 2/22 [00:00<00:01, 13.99it/s, now=None]

t:  12%|████████▊                                                             | 2/16 [00:00<00:00, 15.38it/s, now=None]

                                                                                                                 
                                                                                                                    

t:  17%|███████████▊                          

Moviepy - Building video Extracted_Videos/S2/Silence/sil_451.mp4.
Moviepy - Writing video Extracted_Videos/S2/Silence/sil_451.mp4

Moviepy - Building video Extracted_Videos/S3/Alphabet/a_225.mp4.
Moviepy - Writing video Extracted_Videos/S3/Alphabet/a_225.mp4

Moviepy - Building video Extracted_Videos/S1/Commands/bin_224.mp4.


t:  31%|█████████████████████▉                                                | 5/16 [00:00<00:00, 15.38it/s, now=None]

                                                                                                                 
                                                                                                                    
